In [1]:
!pip install -q --upgrade pip
!pip install -q --upgrade transformers sentencepiece datasets[audio]

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 20.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 129.4/129.4 kB 1.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.4/8.4 MB 45.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 5.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 38.3/38.3 MB 11.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 536.6/536.6 kB 24.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 8.5 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
ibis-framework 7.1.0 requires pyarrow<15,>=2, but you have pyarrow 15.0.0 which is incompatible.


In [14]:
!pip install pydub

In [2]:
!pip install -q torch

In [6]:
from transformers import pipeline
from datasets import load_dataset
import soundfile as sf
import torch

synthesiser = pipeline("text-to-speech", "microsoft/speecht5_tts")

embeddings_dataset = load_dataset("Matthijs/cmu-arctic-xvectors", split="validation")
speaker_embedding = torch.tensor(embeddings_dataset[7306]["xvector"]).unsqueeze(0)
# You can replace this embedding with your own as well.

speech = synthesiser("Hello, my dog is cooler than you!", forward_params={"speaker_embeddings": speaker_embedding})

sf.write("speech.wav", speech["audio"], samplerate=speech["sampling_rate"])


In [7]:
from transformers import SpeechT5Processor, SpeechT5ForTextToSpeech, SpeechT5HifiGan
from datasets import load_dataset
import torch
import soundfile as sf
from datasets import load_dataset

processor = SpeechT5Processor.from_pretrained("microsoft/speecht5_tts")
model = SpeechT5ForTextToSpeech.from_pretrained("microsoft/speecht5_tts")
vocoder = SpeechT5HifiGan.from_pretrained("microsoft/speecht5_hifigan")

inputs = processor(text="Hello, my dog is cute.", return_tensors="pt")

# load xvector containing speaker's voice characteristics from a dataset
embeddings_dataset = load_dataset("Matthijs/cmu-arctic-xvectors", split="validation")
speaker_embeddings = torch.tensor(embeddings_dataset[7306]["xvector"]).unsqueeze(0)

speech1 = model.generate_speech(inputs["input_ids"], speaker_embeddings, vocoder=vocoder)

sf.write("speech1.wav", speech1.numpy(), samplerate=16000)


In [8]:
speech

{'audio': array([ 0.00017243,  0.00036873,  0.00054008, ..., -0.00030211,
        -0.00014355, -0.00032829], dtype=float32),
 'sampling_rate': 16000}

In [9]:
type(speech)

dict

In [10]:
speech1

tensor([1.4566e-05, 3.2417e-04, 6.1454e-04,  ..., 1.1738e-03, 1.1352e-03,
        1.2397e-03])

In [12]:
speech1.numpy()

array([1.4566345e-05, 3.2417476e-04, 6.1454059e-04, ..., 1.1738065e-03,
       1.1352289e-03, 1.2397020e-03], dtype=float32)

In [29]:
!pip install pydub

In [15]:
import os
file_path = "Task2.txt"
with open(file_path, "r", encoding="utf-8") as file:
    text = file.read()
text=text.replace("\n", " ").strip()

In [16]:
from transformers import SpeechT5Processor, SpeechT5ForTextToSpeech, SpeechT5HifiGan
import torch
import re
import soundfile as sf
from datasets import load_dataset
from pydub import AudioSegment
from io import BytesIO

# Load the T5 models
processor = SpeechT5Processor.from_pretrained("microsoft/speecht5_tts")
model = SpeechT5ForTextToSpeech.from_pretrained("microsoft/speecht5_tts")
vocoder = SpeechT5HifiGan.from_pretrained("microsoft/speecht5_hifigan")

# Load xvector containing speaker's voice characteristics from a dataset
embeddings_dataset = load_dataset("Matthijs/cmu-arctic-xvectors", split="validation")
speaker_embeddings = torch.tensor(embeddings_dataset[7306]["xvector"]).unsqueeze(0)

In [17]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [18]:
sentences = nltk.sent_tokenize(text)

In [19]:
sentences[0]

'Summary: Judgment on Complaint under Section 138 of the Negotiable Instruments Act Introduction This text discusses a judgment from the Supreme Court of India regarding a complaint filed under Section 138 of the Negotiable Instruments Act.'

In [20]:
len(sentences)

15

In [21]:
# Function to generate audio for a given text
def generate_audio(text):
    inputs = processor(text=text, return_tensors="pt")
    # Generate speech
    speech = model.generate_speech(inputs["input_ids"],speaker_embeddings, vocoder=vocoder)
    return speech


In [22]:
# Generate audio for each sentence
audios = []
for sent in sentences:
    audio = generate_audio(sent)
    audios+=[audio.numpy()]

In [24]:
from IPython.display import Audio
import numpy as np
Audio(np.concatenate(audios), rate=16000)

In [26]:
merged_audio=np.concatenate(audios)

In [31]:
sf.write("Microsoft_TTS.wav", merged_audio, samplerate=16000)